In [13]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [14]:
import pandas as pd
import numpy as np
pd.options.display.float_format = '{:,.2f}'.format
pd.set_option('display.max_columns', 30)
pd.set_option('display.max_rows', 300)

import time
import os
import datetime
import pickle

from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.wait import WebDriverWait
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.common.keys import Keys

import sys
sys.path.append('..')
from config import CFG
CFG = CFG()

from src.data.get_data import Crawler

In [3]:
crawler = Crawler()
driver = crawler.connect(CFG)

Connecting to Selenium
Waiting on results button
Successfully connected to Selenium


In [11]:
page_box = WebDriverWait(
    driver, CFG.RESULT_BUTTON_WAIT).until(
        EC.element_to_be_clickable((By.CLASS_NAME, "current-page"))
    )
page_box.send_keys('3126')
page_box.send_keys(Keys.RETURN)

In [12]:
dfs = [crawler.make_df()]
while True:
    print(x)
    try:
        crawler.click_button(By.CLASS_NAME, "next-page")
        dfs.append(crawler.make_df())
    except Exception:
        df = pd.concat(dfs)
        break

0


In [18]:
page_list = os.listdir(CFG.PAGE_PATH)
page_list

['page_count_2023-02-10.txt', 'page_count_2023-03-01.txt']

In [21]:
new_pages = [x.split('.')[0].split('_')[-1] for x in page_list]
new_pages

['2023-02-10', '2023-03-01']

In [28]:
new_pages.sort()

In [27]:
new_pages = [new_pages[1]] + [new_pages[0]]
new_pages

['2023-03-01', '2023-02-10']

In [29]:
new_pages

['2023-02-10', '2023-03-01']

In [3]:
class Crawler():
    def __init__(self, url):
        self.driver = webdriver.Chrome()
        self.driver.get(url)
        self.driver.set_window_size(1280, 680)
        self.total = self.driver.find_element(By.CSS_SELECTOR, ".sbcd-total")
        self.current_rows = self.driver.find_element(By.CSS_SELECTOR, ".sbcd-end")
        time.sleep(5)

    def teardown_method(self):
        self.driver.quit()

    def get_iters(self):
        total = self.total.text
        self.iters = math.ceil((int(total)-50) / 50)

    def select_execute_element(self, selector, value, sleep_time):
        button =  self.driver.find_element(selector, value)
        self.driver.execute_script("arguments[0].click();", button)
        time.sleep(sleep_time)

    def exponential_growth(
        self, initial_delay, growth_factor, max_delay, iter
        ):
        return min(initial_delay * (1 + growth_factor) ** iter, max_delay)
        
    def run(self, iters=None):
        self.get_iters()
        if iters is None:
            iters = self.iters
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filters-title", 0.5)
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filter-reset", 2)
        self.select_execute_element(By.CSS_SELECTOR, ".sbcd-filters-title", 0.2)

        for x in range(iters):#range(self.iters):
            sleeptime = self.exponential_growth(0.1, 0.001, 10, x)
            self.select_execute_element(By.CSS_SELECTOR, ".sbcd-next", sleeptime)

        self.page_source =  self.driver.page_source
        pickle.dump(self.page_source, open(f'../data_files/page_source_{self.current_rows.text}_rows.pkl', 'wb'))

    def parse_pagesource(self, page_source=None):
        if page_source is None:
            page_source = self.page_source
        soup = BeautifulSoup(page_source, 'html.parser')
        table = soup.find('table')
        
        df = pd.DataFrame(
            columns=[
                'Date', 'SITE', 'CITY/TOWN', 'EXPECTED SUBSTANCE',
                'FENTANYL TEST STRIP', 'BENZO TEST STRIP', 'FTIR SPECTROMETER'
            ]
        )
        for row in table.tbody.find_all('tr'):    
            # Find all data for each column
            columns = row.find_all('td')
            
            if(columns != []):
                DATE = columns[0].text.strip()
                SITE = columns[1].text.strip()
                CITY_TOWN = columns[2].text.strip()
                EXPECTED_SUBSTANCE = columns[3].text.strip()
                FENTANYL_TEST_STRIP = columns[4].text.strip()
                BENZO_TEST_STRIP = columns[5].text.strip()
                FTIR_SPECTROMETER = columns[6].text.strip()

                df = df.append({
                    'DATE': DATE,  'SITE': SITE,
                    'CITY/TOWN': CITY_TOWN,
                    'EXPECTED SUBSTANCE': EXPECTED_SUBSTANCE,
                    'FENTANYL TEST STRIP': FENTANYL_TEST_STRIP,
                    'BENZO TEST STRIP': BENZO_TEST_STRIP,
                    'FTIR SPECTROMETER': FTIR_SPECTROMETER
                    }, ignore_index=True)
        return df

In [20]:
crawler = Crawler(CFG['URL'])
crawler.run()

In [6]:
df = crawler.parse_pagesource(crawler.page_source)
df

C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17976\3903660942.py:62: FutureWarning: The frame.append method is deprecated

Date                             SITE  CITY/TOWN     EXPECTED SUBSTANCE  \
0   NaN            Outreach Urban Health    Kelowna  Down (Unknown Opioid)   
1   NaN        Burdock House (Penticton)  Penticton          Crack Cocaine   
2   NaN            Get Your Drugs Tested  Vancouver                Unknown   
3   NaN            Get Your Drugs Tested  Vancouver                    GHB   
4   NaN                           Insite  Vancouver        Methamphetamine   
..  ...                              ...        ...                    ...   
95  NaN            Get Your Drugs Tested  Vancouver                Unknown   
96  NaN            Get Your Drugs Tested  Vancouver                   MDMA   
97  NaN            Get Your Drugs Tested  Vancouver       4-Fluorophenibut   
98  NaN  Cammy LaFleur Outreach (Vernon)     Vernon        Methamphetamine   
99  NaN  Cammy LaFleur Outreach (Vernon)     Vernon        Methamphetamine   

   FENTANYL TEST STRIP BENZO TEST STRIP  \
0             Positive         Positive   
1             Negative              N/A   
2             Negative         Negative   
3             Negative              N/A   
4             Negative              N/A   
..                 ...              ...   
95            Positive         Positive   
96            Negative              N/A   
97            Negative              N/A   
98            Negative              N/A   
99            Negative              N/A   

                                    FTIR SPECTROMETER        DATE  
0                          ErythritolCaffeineFentanyl  2022-11-30  
1                                        Cocaine Base  2022-11-30  
2                                  MDAUncertain Match  2022-11-30  
3                            GHB (Wet)Uncertain Match  2022-11-30  
4                     MethamphetamineDimethyl Sulfone  2022-11-30  
..                                                ...         ...  
95  para-FluorofentanylCaffeineErythritolMethamphe...  2022-11-29  
96                                               MDMA  2022-11-29  
97                                   No Library Match  2022-11-29  
98                                    Methamphetamine  2022-11-29  
99                                    Methamphetamine  2022-11-29  

[100 rows x 8 columns]

In [19]:
page_source = pickle.load(open('page_source.pkl', 'rb'))
crawler = Crawler(CFG['URL'])
crawler.parse_pagesource(page_source)

C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({
C:\Users\broug\AppData\Local\Temp\ipykernel_17436\3073532067.py:61: FutureWarning: The frame.append method is deprecated

In [19]:
len(table.tbody.find_all('tr'))

100